Stand: 24.02.25 

- nur kurz zum probieren
- Patriks Github: https://github.com/sgc-kn/dashboards
    - ID Klimamessstation DWD: 02712 (https://opendata.dwd.de/climate_environment/CDC/observations_germany/) 

## Konstanzer Sensoren zum Ausprobieren
- bei dem Diagramm kann man über die Legende die Graphen ein und ausblenden
- über die Tools am rechten Rand kann man in das Diagramm reinzoomen

In [14]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, HoverTool, DatetimeTickFormatter
from bokeh.palettes import Paired12
from bokeh.io import output_notebook, show

from pathlib import Path
import pandas as pd


file_path = Path("..\\data")
file_name = "data_weather_stations_2024.csv"


weather_df = pd.read_csv(file_path / file_name)

print(weather_df.shape, "\n")
print(weather_df.columns, "\n")
display(weather_df.head(), "\n")
print(f"Anzahl der Messorte: {len(weather_df["name"].unique())}\nNamen: {weather_df["name"].unique()}")

(276307, 13) 

Index(['entity_id', 'name', 'dateobserved', 'atmosphericpressure',
       'precipitation', 'relativehumidity', 'temperature', 'winddirection',
       'windspeedavg', 'windspeedmax', 'windspeedmin',
       'surfacetemperaturewintersense', 'temperaturewintersense'],
      dtype='object') 



entity_id           name  \
0  urn:ngsi-ld:WeatherObserved:eui-8cf95720000d35...    Marktstätte   
1  urn:ngsi-ld:WeatherObserved:eui-8cf95720000d2f...    Herose-Park   
2  urn:ngsi-ld:WeatherObserved:eui-8cf95720000d34...  Mainaustrasse   
3  urn:ngsi-ld:WeatherObserved:eui-8cf95720000d34...    Fähre Staad   
4  urn:ngsi-ld:WeatherObserved:eui-8cf95720000d2f...         Hörnle   

                 dateobserved  atmosphericpressure  precipitation  \
0  2024-12-31 23:58:54.822+01                982.5           0.22   
1  2024-12-31 23:55:11.541+01                982.3           0.09   
2  2024-12-31 23:53:21.901+01                981.2           0.04   
3  2024-12-31 23:52:12.075+01                982.0          82.60   
4  2024-12-31 23:51:25.294+01                981.7           0.00   

   relativehumidity  temperature  winddirection  windspeedavg  windspeedmax  \
0              98.2         -1.6             28           0.4           1.1   
1             100.0         -1.3            203           0.6           1.0   
2             100.0         -1.6            232           0.2           0.3   
3             100.0         -1.7            260           0.2           0.6   
4             100.0         -1.9            253           0.2           0.4   

   windspeedmin  surfacetemperaturewintersense  temperaturewintersense  
0           0.1                           0.27                 -1.6309  
1           0.1                            NaN                     NaN  
2           0.0                            NaN                     NaN  
3           0.0                            NaN                     NaN  
4           0.1                            NaN                     NaN

'\n'

Anzahl der Messorte: 12
Namen: ['Marktstätte' 'Herose-Park' 'Mainaustrasse' 'Fähre Staad' 'Hörnle'
 'Riedstrasse' 'Europapark' 'Stadtgarten' 'Bodanplatz' 'Friedrichstrasse'
 'Döbele' 'Stephansplatz']


## Interaktives Bokeh Diagramm:

In [9]:
output_notebook() 

df = weather_df.copy()
df.index = pd.to_datetime(weather_df["dateobserved"], format='ISO8601', utc=True)
stations = df["name"].unique()

# Convert the 'dateobserved' column to datetime using the specified format
#df["dateobserved"] = pd.to_datetime(df["dateobserved"], format='ISO8601')

# Create Bokeh plot with multiple lines (one per station)
p = figure(x_axis_type="datetime", title="Temperaturverlauf pro Station", width=1200, height=600)
p.xaxis.axis_label = "Datum"
p.yaxis.axis_label = "Temperatur (°C)"

# Assign distinct colors to stations
colors = ["blue", "red", "green", "purple", "orange", "brown", "pink", "cyan"]
station_colors = dict(zip(stations, Paired12))

# Add lines for each station
for station in stations:
    station_data = df[df["name"] == station]
    source = ColumnDataSource(data=dict(
        x=station_data.index,
        y=station_data["temperature"],
        #name=df["name"] * len(station_data)
    ))
    
    p.line('x', 'y', source=source, line_width=2, legend_label=station, color=station_colors[station])
    p.scatter('x', 'y', source=source, size=5, color=station_colors[station], legend_label=station)

# Configure legend
p.legend.title = "Stationen"
p.legend.location = "top_right"
p.legend.click_policy = "hide"  # Allow hiding of individual lines

# Add hover tool for better interaction
hover = HoverTool(
    tooltips=[("Temperatur", "@y")]
)
p.add_tools(hover)

p.y_scale

# Adjust the datetime formatting on the x-axis to show month and year properly
p.xaxis.formatter = DatetimeTickFormatter(
    minutes="%Y-%m-%d %H:%M",
    hours="%Y-%m-%d %H:%M",
    days="%Y-%m-%d",
    months="%Y-%m",
    years="%Y"
)

p.y_range.end = 40

# Show the plot
show(p)



Loading BokehJS ...